In [1]:
import pandas as pd
import altair as alt
from datetime import datetime
import warnings
warnings.filterwarnings('ignore')

In [2]:
# ECDC Europai oltasi adatok
df = pd.read_csv('https://opendata.ecdc.europa.eu/covid19/vaccine_tracker/csv/data.csv')

In [41]:
# Transzformaljuk a datumot
df['date'] = df["YearWeekISO"].map(lambda x: datetime.fromisocalendar(int(x.split('-W')[0]),int(x.split('-W')[1]),7))

In [42]:
# Fokuszaljunk a Magyar adatokra eloszor.
data = df[df['ReportingCountry']=="HU"]

In [43]:
# Allitsuk elo a beadott elso oltasok kumulativ osszeget
data['First doses administered'] = data.groupby("Vaccine")['FirstDose'].cumsum()

In [44]:
#Rajzoltassuk ki.
alt.Chart(data).mark_line().encode(
    x="date:T",
    y="First doses administered:Q",
    color="Vaccine:N"
)

alt.Chart(...)

In [45]:
# Valami nem stimmel, vajon mi?
data["TargetGroup"].unique()

array(['ALL', 'Age18_24', 'Age25_49', 'Age50_59', 'Age60_69', 'Age70_79',
       'Age80+', 'AgeUNK', 'HCW', 'LTCF', 'Age<18'], dtype=object)

In [46]:
# Szamitsuk ujra, ezuttal korcsoportokra tekintettel
data['First doses administered for target group'] = data.groupby(["Vaccine",'TargetGroup'])['FirstDose'].cumsum()

In [47]:
# Rajzoltassuk ki
alt.Chart(data[data['TargetGroup']=="ALL"]).mark_line().encode(
    x="date:T",
    y="First doses administered for target group:Q",
    color="Vaccine:N"
)

alt.Chart(...)

In [48]:
# Ugyanez korcsoportok szerint
alt.Chart(data[~data['TargetGroup'].isin(["AgeUNK",'LTCF','HCW'])]).mark_line().encode(
    x="date:T",
    y="First doses administered for target group:Q",
    color="Vaccine:N"
).properties(
    width=200
).facet(
    facet='TargetGroup:N',
    columns=2
)

alt.FacetChart(...)

In [49]:
# Oldjuk fel az y tengelyt
alt.Chart(data[~data['TargetGroup'].isin(["AgeUNK",'LTCF','HCW'])]).mark_line().encode(
    x="date:T",
    y="First doses administered for target group:Q",
    color="Vaccine:N"
).properties(
    width=200
).facet(
    facet='TargetGroup:N',
    columns=2
).resolve_scale(y='independent')

alt.FacetChart(...)

In [12]:
# Talan hasznosabb egy stacked area chart
alt.Chart(data[data.TargetGroup=="ALL"]).mark_area().encode(
    x="date:T",
    y="First doses administered for target group:Q",
    color="Vaccine:N"
)

alt.Chart(...)

In [13]:
# Ugyanigy korcsoportonkent is.
alt.Chart(data[~data['TargetGroup'].isin(["AgeUNK",'LTCF','HCW'])]).mark_area().encode(
    x="date:T",
    y="First doses administered for target group:Q",
    color="Vaccine:N"
).properties(
    width=200
).facet(
    facet='TargetGroup:N',
    columns=2
).resolve_scale(y='independent')

alt.FacetChart(...)

In [14]:
# Nezzuk a nemzetkozi adatokat, fokuszaljunk az aggregatumra
international = df[df['TargetGroup']=="ALL"]

In [15]:
# Szamitsunk aranyokat - a nepesseg hany szazaleka kapott oltast
international['Oltottak aranya - elso dozis'] = international['FirstDose']/international["Population"]

In [16]:
# Adjuk ossze a kulonbozo tipusu oltasokat, majd keszitsunk kumulativ osszeget
transformed = international.groupby(['ReportingCountry','date'])['Oltottak aranya - elso dozis'].sum().reset_index()

In [17]:
transformed['Oltottak aranya']=transformed.groupby(['ReportingCountry'])['Oltottak aranya - elso dozis'].cumsum()

In [18]:
#Rajzoltassuk ki.
alt.Chart(transformed).mark_line().encode(
    x="date:T",
    y="Oltottak aranya:Q",
    color="ReportingCountry:N"
)

alt.Chart(...)

In [19]:
# Egyreszt zsufolt, masreszt egyes orszagok nem jelentik kulon a dozisokat, igy 1 fole megy az arany. Szukitsuk kicsit, pl nehany erdekesebb orszagra
# Rajzoltassuk ki.
alt.Chart(transformed[transformed['ReportingCountry'].isin(['HU','AT','IS'])]).mark_line().encode(
    x="date:T",
    y="Oltottak aranya:Q",
    color="ReportingCountry:N"
)

alt.Chart(...)

In [20]:
# Ki mikor kapott oltast?
magyararanyok=df[df['ReportingCountry']=='HU']
magyararanyok['Oltottak aranya - elso dozis'] = magyararanyok['FirstDose']/magyararanyok["Denominator"]

In [21]:
data = magyararanyok.groupby(['TargetGroup',"date"])['Oltottak aranya - elso dozis'].sum().reset_index()

base = alt.Chart(data[~data['TargetGroup'].isin(['ALL',"AgeUNK",'LTCF','HCW'])]).mark_circle(opacity=0.5).encode(
    alt.X('date:T'),
    alt.Y('Oltottak aranya - elso dozis:Q'),
    alt.Color('TargetGroup:N')
)

base + base.transform_loess('date', 'Oltottak aranya - elso dozis', groupby=['TargetGroup']).mark_line(size=1)

alt.LayerChart(...)

In [22]:
# Hogyan alakul az oltatlanok aranya az egyes korcsoportokon belul?
data['Oltatlanok aranya'] = 1-data.groupby(['TargetGroup'])['Oltottak aranya - elso dozis'].cumsum()

In [23]:
alt.Chart(data[~data['TargetGroup'].isin(["AgeUNK",'LTCF','HCW'])]).mark_line().encode(
    x="date:T",
    y="Oltatlanok aranya:Q",
    color="TargetGroup:N"
)

alt.Chart(...)

In [24]:
# Hol mivel oltanak?
mivel = international[international['TargetGroup']=='ALL'].groupby(['ReportingCountry',"Vaccine"])['Oltottak aranya - elso dozis'].sum().reset_index()

In [25]:
alt.Chart(mivel).mark_bar().encode(
    x='Oltottak aranya - elso dozis',
    y='ReportingCountry',
    color='Vaccine'
)

alt.Chart(...)

In [26]:
proper = (mivel.groupby('ReportingCountry').sum()<1).reset_index()

In [27]:
countries = proper[proper['Oltottak aranya - elso dozis']]['ReportingCountry'].tolist()

In [28]:
alt.Chart(mivel[mivel['ReportingCountry'].isin(countries)]).mark_bar().encode(
    x='Oltottak aranya - elso dozis',
    y='ReportingCountry',
    color='Vaccine'
)

alt.Chart(...)

In [52]:
# Hol kit mivel oltanak?
df['Oltottak aranya - elso dozis'] = df['FirstDose']/df["Denominator"]
plotra = df[~df['TargetGroup'].isin(["AgeUNK",'LTCF','HCW','1_Age60+', '1_Age<60'])].groupby(['ReportingCountry','TargetGroup','Vaccine'])['Oltottak aranya - elso dozis'].sum().reset_index()



In [54]:
alt.Chart(plotra[plotra['ReportingCountry'].isin(countries)]).mark_bar().encode(
    x='Oltottak aranya - elso dozis',
    y='ReportingCountry',
    color='Vaccine'
).properties(
    width=200
).facet(
    facet='TargetGroup:N',
    columns=2
)

alt.FacetChart(...)